# Lab 1 — Tiny VLM Adversarial Cost Challenge

## Overview

Welcome to the ML Security Lab! In this lab, you'll implement adversarial attacks against a Vision-Language Model (VLM) using the custom dataset and a frozen TinyCLIP scorer.

### Objective
Your task is to build an attack function that can manipulate either:
- **Caption tokens** (text modifications)
- **Image pixels** (visual modifications)
- **Both** (multimodal attack)

The goal is to flip the model's decision (match → no-match or vice versa) while minimizing the attack cost.

### Constraints
- **T_MAX = 10**: Maximum token edits per sample
- **P_MAX = 100**: Maximum pixel edits per sample  
- **Q_MAX = 100**: Maximum queries per sample
- **Evaluation**: Public leaderboard (1,000 val pairs) + Private leaderboard (1,000 test pairs)

### Scoring
Your attack will be evaluated based on:
1. **Success Rate**: Percentage of samples where you successfully flip the decision
2. **Cost Efficiency**: Lower total cost (token edits + pixel edits + queries) is better
3. **Attack Budget**: Must stay within the specified limits

In [1]:
import os
import zipfile

# Check if 'images' directory or 'val_pairs.json' file is missing
if not os.path.exists('images') or not os.path.exists('val_pairs.json'):
    print("Required data not found. Extracting 'data.zip'...")
    
    # Check if 'data.zip' exists
    if os.path.exists('data.zip'):
        with zipfile.ZipFile('data.zip', 'r') as zip_ref:
            zip_ref.extractall()  # Extract all files in the current directory
        print("Extraction complete!")
    else:
        print("Error: 'data.zip' not found. Please ensure the file is in the current directory.")
else:
    print("All required data is already present.")

All required data is already present.


In [2]:
# Import required libraries
import numpy as np
import pandas as pd
from PIL import Image
import PIL
import torch
import torch.nn.functional as F
from tqdm.auto import tqdm
import open_clip
from datasets import load_dataset
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import accuracy_score
from sklearn.linear_model import LogisticRegression
import json
import random
import os
from typing import List, Tuple, Dict, Optional
import warnings
import requests
from urllib.parse import urlparse
import hashlib
from collections import defaultdict
warnings.filterwarnings('ignore')

# Set random seeds for reproducibility
np.random.seed(42)
torch.manual_seed(42)
random.seed(42)

print("All packages imported successfully!")
print(f"PyTorch version: {torch.__version__}")
print(f"CUDA available: {torch.cuda.is_available()}")

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

/home/lucas/adverserial-cybersecurity/.venv/lib64/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


All packages imported successfully!
PyTorch version: 2.8.0+cu128
CUDA available: True
Using device: cuda


In [3]:
# Data Loading
print("Loading validation data...")

# Load validation pairs from JSON
with open('val_pairs.json', 'r') as f:
    val_pairs = json.load(f)

print(f"Loaded {len(val_pairs)} validation pairs")

# Helper function to load images
def load_image_from_pair(pair: dict) -> Image.Image:
    """Load image from the pair dictionary using image_path"""
    return Image.open(pair['image_path']).convert('RGB')

# Sample a few pairs to verify data loading
print("\nSample validation pairs:")
for i in range(3):
    pair = val_pairs[i]
    print(f"  Image ID: {pair['image_id']}, Path: {pair['image_path']}")
    print(f"  Caption: {pair['caption'][:50]}..., Match: {pair['is_match']}")
    print()

print(f"Data distribution:")
labels = [pair['is_match'] for pair in val_pairs]
print(f"  Match (True): {sum(labels)}")
print(f"  No-match (False): {len(labels) - sum(labels)}")
print(f"  Balance: {sum(labels)/len(labels):.2%} positive")

Loading validation data...
Loaded 1000 validation pairs

Sample validation pairs:
  Image ID: 38137, Path: images/val/000000119402.jpg
  Caption: A gold bus traveling on a single lane road..., Match: True

  Image ID: 15194, Path: images/val/000000404780.jpg
  Caption: Two women in the snow on skis in front of a large ..., Match: False

  Image ID: 19082, Path: images/val/000000148898.jpg
  Caption: A man jumping a brown horse over an obstacle...., Match: False

Data distribution:
  Match (True): 500
  No-match (False): 500
  Balance: 50.00% positive


In [4]:
# TinyCLIP Scorer Implementation
print("Loading CLIP model...")

# Try to load TinyCLIP, fallback to OpenCLIP ViT-B/32 if failed
try:
    # Attempt to load TinyCLIP from HuggingFace hub
    model, preprocess, tokenizer = open_clip.create_model_and_transforms(
        "hf-hub:microsoft/TinyCLIP-ViT-8M-16-Text-3M-YFCC15M"
    )
    print("Successfully loaded TinyCLIP model")
except Exception as e:
    print(f"Failed to load TinyCLIP: {e}")
    print("Falling back to OpenCLIP ViT-B/32...")

    model, preprocess, tokenizer = open_clip.create_model_and_transforms(
        "ViT-B-32", 
        pretrained="laion2b_s34b_b79k"
    )
    print("Successfully loaded OpenCLIP ViT-B/32")

# Move model to device
model = model.to(device)
model.eval()

print(f"Model loaded on: {device}")


Loading CLIP model...
Failed to load TinyCLIP: Failed initial config/weights load from HF Hub microsoft/TinyCLIP-ViT-8M-16-Text-3M-YFCC15M: Failed to download file (open_clip_config.json) for microsoft/TinyCLIP-ViT-8M-16-Text-3M-YFCC15M. Last error: 404 Client Error. (Request ID: Root=1-68f3fa54-506b74995df7f32878ae3dd2;20d2445e-7a7f-427f-8fd3-16ecbef3a695)

Repository Not Found for url: https://huggingface.co/microsoft/TinyCLIP-ViT-8M-16-Text-3M-YFCC15M/resolve/main/open_clip_config.json.
Please make sure you specified the correct `repo_id` and `repo_type`.
If you are trying to access a private or gated repo, make sure you are authenticated. For more details, see https://huggingface.co/docs/huggingface_hub/authentication
Falling back to OpenCLIP ViT-B/32...
Successfully loaded OpenCLIP ViT-B/32
Model loaded on: cuda


In [5]:
def clip_embed(image: Image.Image, caption: str) -> float:
    """
    Compute cosine similarity between image and text embeddings.
    
    Args:
        image: PIL Image
        caption: Text string
    
    Returns:
        Cosine similarity score between normalized embeddings
    """
    with torch.no_grad():
        # Preprocess image
        image_tensor = preprocess(image).unsqueeze(0).to(device)
        
        # Tokenize text properly using open_clip tokenizer
        text_tokens = open_clip.tokenize([caption]).to(device)
        
        # Get embeddings
        image_features = model.encode_image(image_tensor)
        text_features = model.encode_text(text_tokens)
        
        # Normalize embeddings
        image_features = F.normalize(image_features, dim=-1)
        text_features = F.normalize(text_features, dim=-1)
        
        # Compute cosine similarity
        similarity = (image_features @ text_features.T).item()
        
    return similarity

# Test the embedding function
print("\nTesting CLIP embedding function...")
test_pair = val_pairs[0]
test_image = load_image_from_pair(test_pair)
test_similarity = clip_embed(test_image, test_pair['caption'])
print(f"Sample similarity score: {test_similarity:.4f} (Expected match: {test_pair['is_match']})")

# Test on a few more samples
print("\nTesting on more samples:")
for i in range(3):
    pair = val_pairs[i]
    image = load_image_from_pair(pair)
    similarity = clip_embed(image, pair['caption'])
    print(f"Sample {i+1}: similarity={similarity:.4f}, match={pair['is_match']}")


Testing CLIP embedding function...
Sample similarity score: 0.3695 (Expected match: True)

Testing on more samples:
Sample 1: similarity=0.3526, match=True
Sample 2: similarity=0.0343, match=False
Sample 3: similarity=0.0774, match=False


In [6]:
print(open_clip.tokenize)

<function tokenize at 0x7f810b5fe020>


In [7]:
# Calibration: Fit logistic regression to get alpha, beta parameters
print("Calibrating scorer with logistic regression...")

# Use first 200 samples for calibration
tune_slice = val_pairs[:200]
print(f"Using {len(tune_slice)} samples for calibration")

# Compute similarities for calibration
similarities = []
ground_truths = []

print("Computing similarities for calibration...")
for pair in tqdm(tune_slice, desc="Calibration"):
    image = load_image_from_pair(pair)
    similarity = clip_embed(image, pair['caption'])
    similarities.append(similarity)
    ground_truths.append(int(pair['is_match']))

similarities = np.array(similarities).reshape(-1, 1)
ground_truths = np.array(ground_truths)

# Fit logistic regression: sigmoid(alpha * cosine + beta)
lr = LogisticRegression()
lr.fit(similarities, ground_truths)

# Extract alpha and beta
alpha = lr.coef_[0][0]  # Coefficient for similarity
beta = lr.intercept_[0]  # Intercept

print(f"Calibration complete!")
print(f"   Alpha (slope): {alpha:.4f}")
print(f"   Beta (intercept): {beta:.4f}")

# Test calibration
def sigmoid(x):
    return 1 / (1 + np.exp(-x))

test_similarities = similarities[:5].flatten()
test_labels = ground_truths[:5]
calibrated_probs = sigmoid(alpha * test_similarities + beta)

print(f"\nCalibration test:")
for i in range(5):
    print(f"  Sim: {test_similarities[i]:.4f} → Prob: {calibrated_probs[i]:.4f}, True: {test_labels[i]}")

Calibrating scorer with logistic regression...
Using 200 samples for calibration
Computing similarities for calibration...


Calibration: 100%|██████████| 200/200 [00:03<00:00, 61.83it/s]

Calibration complete!
   Alpha (slope): 6.6231
   Beta (intercept): -1.1130

Calibration test:
  Sim: 0.3561 → Prob: 0.7765, True: 1
  Sim: 0.0343 → Prob: 0.2920, True: 0
  Sim: 0.0802 → Prob: 0.3585, True: 0
  Sim: 0.1899 → Prob: 0.5362, True: 0
  Sim: 0.3586 → Prob: 0.7794, True: 1


In [8]:
from scipy.ndimage import label

# BlackBox API Implementation
import editdistance  # For Levenshtein distance

class BlackBoxAPI:
    """
    Black-box API for the VLM scorer with query budget tracking and cost calculation.
    """
    
    def __init__(self, alpha: float, beta: float, q_max: int = 200):
        """
        Initialize the black-box API.
        
        Args:
            alpha: Logistic regression slope parameter
            beta: Logistic regression intercept parameter  
            q_max: Maximum queries allowed per sample
        """
        self.alpha = alpha
        self.beta = beta
        self.q_max = q_max
        self.query_count = 0
        
    def score(self, image_uint8: np.ndarray, caption_str: str) -> float:
        """
        Score image-caption pair and return probability.
        
        Args:
            image_uint8: Image as uint8 numpy array (H, W, C)
            caption_str: Caption string
            
        Returns:
            Probability in [0, 1] using sigmoid(alpha * cosine + beta)
        """
        if self.query_count >= self.q_max:
            raise RuntimeError(f"Query budget exceeded! Used {self.query_count}/{self.q_max}")
            
        # Convert numpy array to PIL Image
        image_pil = Image.fromarray(image_uint8)
        
        # Get cosine similarity
        cosine_sim = clip_embed(image_pil, caption_str)
        
        # Apply calibrated sigmoid
        logit = self.alpha * cosine_sim + self.beta
        probability = 1 / (1 + np.exp(-logit))
        
        self.query_count += 1
        
        return probability
    
    def reset_query_count(self):
        """Reset query counter for new sample."""
        self.query_count = 0
        
    def get_remaining_queries(self) -> int:
        """Get remaining query budget."""
        return self.q_max - self.query_count

# Cost Functions
def token_edit_cost(original: str, modified: str) -> int:
    """
    Compute token-level Levenshtein distance using CLIP tokenizer.
    
    Args:
        original: Original caption
        modified: Modified caption
        
    Returns:
        Number of token edits (insertions, deletions, substitutions)
    """
    # Use CLIP tokenizer for more accurate tokenization
    orig_tokens = open_clip.tokenize([original], context_length=77)[0].numpy()
    mod_tokens = open_clip.tokenize([modified], context_length=77)[0].numpy()
    
    # Remove padding tokens (0s) and special tokens for fair comparison
    # Keep only actual content tokens
    orig_tokens = orig_tokens[orig_tokens != 0]
    mod_tokens = mod_tokens[mod_tokens != 0]
    
    return editdistance.eval(orig_tokens.tolist(), mod_tokens.tolist())

def pixel_edit_cost(original: np.ndarray, modified: np.ndarray) -> int:
    """
    Compute number of changed pixels with reduced cost for continuous regions.
    
    Args:
        original: Original image as uint8 numpy array
        modified: Modified image as uint8 numpy array
        
    Returns:
        Adjusted cost based on number of changed pixels, with reduced cost for continuous regions.
    """
    # Find the difference mask
    diff_mask = np.any(original != modified, axis=-1)
    
    # Label connected components in the difference mask
    labeled_regions, num_features = label(diff_mask)
    
    # Count pixels in each connected region
    total_cost = 0
    for region_id in range(1, num_features + 1):
        region_size = np.sum(labeled_regions == region_id)
        if region_size > 0:
            # Full cost for the first pixel, half cost for the rest
            total_cost += 1 + (region_size - 1) * 0.5
    
    return int(total_cost)

# Test the BlackBox API
print("Testing BlackBox API...")

# Initialize API with calibrated parameters
api = BlackBoxAPI(alpha, beta, q_max=200)

# Test on a sample
test_pair = val_pairs[0]
test_image = load_image_from_pair(test_pair)
test_image_uint8 = np.array(test_image)

# Get score
score = api.score(test_image_uint8, test_pair['caption'])
print(f"API Score: {score:.4f} (Expected match: {test_pair['is_match']})")
print(f"Queries used: {api.query_count}/{api.q_max}")

# Test cost functions
original_caption = "A cat sitting on a mat"
modified_caption = "A dog standing on a rug" 
token_cost = token_edit_cost(original_caption, modified_caption)
print(f"\nToken edit cost example:")
print(f"  Original: '{original_caption}'")  
print(f"  Modified: '{modified_caption}'")
print(f"  Cost: {token_cost} token edits")

# Test pixel cost (create a simple modification)
original_img = np.zeros((100, 100, 3), dtype=np.uint8)
modified_img = original_img.copy()
modified_img[10:20, 10:20] = 255  # Change a 10x10 region
pixel_cost = pixel_edit_cost(original_img, modified_img)
print(f"\nPixel edit cost example:")
print(f"  Modified {pixel_cost} pixels in 100x100 image")

Testing BlackBox API...
API Score: 0.7881 (Expected match: True)
Queries used: 1/200

Token edit cost example:
  Original: 'A cat sitting on a mat'
  Modified: 'A dog standing on a rug'
  Cost: 3 token edits

Pixel edit cost example:
  Modified 50 pixels in 100x100 image


## Your Task: Implement Adversarial Attacks

### Attack Function Template

Replace the trivial baseline in the `attack()` function with sophisticated adversarial attacks:

```python
def attack(image_np_uint8, caption_str, api, budgets):
    # Your attack implementation here!
    # You can modify:
    # - Caption tokens (text modifications)  
    # - Image pixels (visual modifications)
    # - Both (multimodal attack)
    
    # Stay within budgets:
    # - budgets['T_MAX'] = 10  token edits
    # - budgets['P_MAX'] = 100 pixel edits
    # - budgets['Q_MAX'] = 100 queries
    
    return {
        'success': success,      # bool: did you flip the decision?
        'image': final_image,    # np.array: attacked image
        'caption': final_caption, # str: attacked caption  
        'token_cost': token_cost, # int: tokens changed
        'pixel_cost': pixel_cost, # int: pixels changed
        'query_cost': query_cost  # int: API calls made
    }
```

### Attack Strategies to Consider

- **Text Attacks**: Synonym replacement, word insertion/deletion, semantic paraphrasing
- **Image Attacks**: Adversarial noise, targeted pixel modifications, patch attacks
- **Query Optimization**: Gradient-free optimization, genetic algorithms, hill climbing
- **Multimodal**: Combined text+image attacks for maximum effectiveness

### Evaluation Metrics

Your attack will be scored as: **ASR - 0.5×ANC - 0.1×(AQ/Q_MAX)**

- **ASR**: Attack Success Rate (higher is better)
- **ANC**: Average Number of Changes (lower is better) 
- **AQ**: Average Queries (lower is better)

### Next Steps

1. **Implement your attack** in the `attack()` function above
2. **Test locally** using the evaluation framework  
3. **Run on full dataset** by changing `max_samples=None`

Good luck! 

### <span style="color:red">**FILL THIS CODE BLOCK**</span>

In [9]:
# with torch.no_grad():
#         # Preprocess image
#         image_tensor = preprocess(image).unsqueeze(0).to(device)
        
#         # Tokenize text properly using open_clip tokenizer
#         text_tokens = open_clip.tokenize([caption]).to(device)
        
#         # Get embeddings
#         image_features = model.encode_image(image_tensor)
#         text_features = model.encode_text(text_tokens)
        
#         # Normalize embeddings
#         image_features = F.normalize(image_features, dim=-1)
#         text_features = F.normalize(text_features, dim=-1)
        
#         # Compute cosine similarity
#         similarity = (image_features @ text_features.T).item()
        
#     return similarity

In [10]:
def calc_similarity(image_features, text_features) -> float:
    with torch.no_grad():
        image_features = F.normalize(image_features, dim=-1)
        text_features = F.normalize(text_features, dim=-1)
        
        # Compute cosine similarity
        similarity = (image_features @ text_features.T).item()
        
    return similarity

In [11]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# device = "cpu"
model.to(device)
def encode_text(text:str):
    text_tokens = open_clip.tokenize([text]).to(device)
    text_features = model.encode_text(text_tokens).to("cpu")
    # free up space on device
    text_tokens = None
    return text_features

In [12]:
# load nounlist.csv
nounlist = pd.read_csv('nounlist.csv', header=None)
nounlist.columns = ['nouns']
# delete all but a 300 rows
# nounlist = nounlist.head(300)

#apply function encode_text to each noun and put in new column
with torch.no_grad():
    nounlist['encoded'] = nounlist['nouns'].apply(encode_text)
nounlist

nouns                                            encoded
0           ATM  [[tensor(0.1433), tensor(-0.2801), tensor(-0.1...
1            CD  [[tensor(0.2364), tensor(-0.1194), tensor(-0.4...
2           SUV  [[tensor(-0.3482), tensor(-0.1286), tensor(-0....
3            TV  [[tensor(-0.1657), tensor(-0.3337), tensor(-0....
4      aardvark  [[tensor(0.4404), tensor(-0.2014), tensor(-0.0...
...         ...                                                ...
6796        zoo  [[tensor(-0.1076), tensor(-0.0910), tensor(-0....
6797  zoologist  [[tensor(-0.0608), tensor(0.0313), tensor(0.00...
6798    zoology  [[tensor(-0.0363), tensor(0.0437), tensor(-0.2...
6799  zoot-suit  [[tensor(0.1474), tensor(-0.1697), tensor(-0.4...
6800   zucchini  [[tensor(-0.2350), tensor(-0.0220), tensor(0.0...

[6801 rows x 2 columns]

In [30]:
# pip install spacy inflect
# python -m spacy download en_core_web_sm

import spacy
import inflect

nlp = spacy.load("en_core_web_sm")
infl = inflect.engine()

NOUN_TAGS = {"NN", "NNS", "NNP", "NNPS"}

def _match_casing(src: str, repl: str) -> str:
    if src.isupper():
        return repl.upper()
    if src.istitle():
        return repl.title()
    return repl

def _maybe_pluralize(base: str, tag: str) -> str:
    if tag in {"NNS", "NNPS"}:
        return infl.plural(base) or base + "s"
    return base

def attack_replace_nouns(caption: str, replace_word = "") -> str:
    doc = nlp(caption)
    out = []
    for tok in doc:
        if tok.tag_ in NOUN_TAGS:
            word = replace_word
            if word != "":
                word = _maybe_pluralize(replace_word, tok.tag_)
                word = _match_casing(tok.text, word)
            out.append(word + tok.whitespace_)
        else:
            out.append(tok.text_with_ws)
    return "".join(out)

# examples
print(attack_replace_nouns("A small dog runs across the field."))
# -> "A small cat runs across the cat."
print(attack_replace_nouns("John's red cars were parked in New York"))
print(attack_replace_nouns("A man standing in front of a refrigerator freezer."))
# -> "Cat's red cats were parked in Cat Cat."


A small  runs across the .
's red  were parked in  
A  standing in  of a  .


In [31]:
ADJ_TAGS = {"JJ", "JJR", "JJS"}

def _match_casing(src: str, repl: str) -> str:
    if src.isupper():
        return repl.upper()
    if src.istitle():
        return repl.title()
    return repl

def _degree_wrap(base_adj: str, tag: str) -> str:
    # Safer than trying to inflect irregulars: use "more/most" wrappers
    if tag == "JJR":
        return f"more {base_adj}"
    if tag == "JJS":
        return f"most {base_adj}"
    return base_adj

def attack_replace_adjectives(caption: str, replacement_adj: str = "") -> str:
    doc = nlp(caption)
    out = []
    for tok in doc:
        if tok.tag_ in ADJ_TAGS:
            repl = _degree_wrap(replacement_adj, tok.tag_)
            # If the replacement is multiword (e.g., "more fluffy"), match casing of the first word only
            parts = repl.split(" ")
            parts[0] = _match_casing(tok.text, parts[0])
            repl = " ".join(parts)
            # Preserve original whitespace
            out.append(repl + tok.whitespace_)
        else:
            out.append(tok.text_with_ws)
    return "".join(out)

In [32]:
def remove_caption(caption: str) -> str:
    return "".join(caption.split(" ")[:-10])

In [33]:
def caption_remove_attack(original_caption: str, image: np.ndarray, original_label, api) -> str:
    """
    Caption attack that removes words from the original caption to flip the model's prediction.
    
    Args:
        original_caption: The original caption string.
        image: The original image as a uint8 numpy array.
        original_label: The original label (True/False).
        
    Returns:
        The modified caption after removing words.
    """
    words = original_caption.split()
    best_caption = original_caption
    best_score = api.score(image, best_caption)
    
    improved = True
    while improved and len(words) > 1:
        improved = False
        for i in range(len(words)):
            # Create a new caption by removing the i-th word
            new_caption = ' '.join(words[:i] + words[i+1:])
            new_score = api.score(image, new_caption)
            
            # Check if this removal improves the score towards flipping the label
            if (original_label and new_score < 0.5) or (not original_label and new_score > 0.5):
                best_caption = new_caption
                best_score = new_score
                words = new_caption.split()
                improved = True
                break  # Restart the process after a successful removal
                
    return best_caption

In [ ]:
def caption_attack(original_caption: str, image: np.ndarray, orginal_label) -> str:
    
    image_tensor = preprocess(Image.fromarray(image)).unsqueeze(0).to(device)
    image_features = model.encode_image(image_tensor)
    if orginal_label == False:
        best_sim = -1
    else:
        best_sim = 1
    
    for index, row in nounlist.iterrows():
        #print(best_sim)
        noun = row['nouns']
        text_features = row['encoded']
        sim = calc_similarity(image_features.to("cpu"), text_features.to("cpu"))
        if (sim < best_sim and orginal_label == True) or (sim > best_sim and orginal_label == False):
            best_sim = sim
            best_noun = noun
    #print(f"Best noun to add: {best_noun} with similarity {best_sim}")

    final_caption = attack_replace_nouns(original_caption, best_noun)

    return final_caption

In [ ]:
def attack(image_np_uint8: np.ndarray, caption_str: str, api: BlackBoxAPI, budgets: dict, verbose=False) -> dict:
    """
    Student attack function to implement adversarial attacks.
    
    Args:
        image_np_uint8: Original image as uint8 numpy array (H, W, C)
        caption_str: Original caption string
        api: BlackBoxAPI instance for querying the model
        budgets: Dictionary with 'T_MAX', 'P_MAX', 'Q_MAX' limits
        
    Returns:
        Dictionary with:
        - 'success': bool, whether attack succeeded (flipped decision)
        - 'image': np.ndarray, final attacked image  
        - 'caption': str, final attacked caption
        - 'token_cost': int, number of token edits used
        - 'pixel_cost': int, number of pixel edits used
        - 'query_cost': int, number of queries used
    """
    
    # TRIVIAL BASELINE - Students should replace this!
    # This baseline just returns the original inputs without any attack
    
    original_image = image_np_uint8.copy()
    original_caption = caption_str
    
    
    
    # Get original score to determine target (flip the decision)
    original_score = api.score(original_image, original_caption)
    

    # For this baseline, we don't actually perform any attack
    # Students should implement sophisticated attacks here!
    
    # TODO: IMPLEMENT YOUR ATTACK HERE!
    # You can modify:
    # - Caption tokens (text modifications)  
    # - Image pixels (visual modifications)
    # - Both (multimodal attack)
    
    # Stay within budgets:
    # - budgets['T_MAX'] = maximum token edits
    # - budgets['P_MAX'] = maximum pixel edits
    # - budgets['Q_MAX'] = maximum queries
    
    # Attack Strategies to Consider:
    # - Text Attacks: Synonym replacement, word insertion/deletion, semantic paraphrasing
    # - Image Attacks: Adversarial noise, targeted pixel modifications, patch attacks
    # - Query Optimization: Gradient-free optimization, genetic algorithms, hill climbing
    # - Multimodal: Combined text+image attacks for maximum effectiveness

    original_label = original_score > 0.5
    

    #final_image = image_attack(original_image, original_caption, original_label, pixels_changed=100, epsilon=2, steps=15)        # Comment out this line when implementing image attacks
    final_image = original_image  # Placeholder: No image attack implemented yet
    final_caption = caption_attack(original_caption, original_image, original_label)    # Comment out this line when implementing text attacks
    #final_caption = caption_remove_attack(original_caption, original_image, original_label, api)    # Comment out this line when implementing text attacks
    #final_caption = attack_replace_nouns(original_caption)
    #final_caption = attack_replace_adjectives(original_caption)
    #final_caption = remove_caption(original_caption)
    # Get final score  
    final_score = api.score(final_image, final_caption)
    if verbose:
        print(f"Original caption: {original_caption}")
        print(f"Original score: {original_score:.4f}, Original label: {original_label}")
        print(f"Final score: {final_score:.4f}")
    
    # Check if attack succeeded (decision flipped)
    original_decision = original_score > 0.5
    final_decision = final_score > 0.5
    success = (original_decision != final_decision)
    
    # Calculate costs
    token_cost = token_edit_cost(original_caption, final_caption)
    pixel_cost = pixel_edit_cost(original_image, final_image)
    query_cost = api.query_count
    
    return {
        'success': success,
        'image': final_image,
        'caption': final_caption,
        'token_cost': token_cost,
        'pixel_cost': pixel_cost,  
        'query_cost': query_cost,
        'original_score': original_score,
        'final_score': final_score
    }

print("Attack function defined (TRIVIAL BASELINE)")
print("   Students should replace the trivial implementation with sophisticated attacks!")
print("   Current baseline: Returns original inputs unchanged (0% success rate expected)")

# Test the attack function
print("\nTesting attack function...")
test_pair = val_pairs[0]
test_image = np.array(load_image_from_pair(test_pair))

# Create fresh API instance  
test_api = BlackBoxAPI(alpha, beta, q_max=100)

attack_budgets = {
    'T_MAX': 10,     # Maximum token edits per sample
    'P_MAX': 100,   # Maximum pixel edits per sample  
    'Q_MAX': 100    # Maximum queries per sample
}

result = attack(test_image, test_pair['caption'], test_api, attack_budgets)
print(f"Attack success: {result['success']}")

Attack function defined (TRIVIAL BASELINE)
   Students should replace the trivial implementation with sophisticated attacks!
   Current baseline: Returns original inputs unchanged (0% success rate expected)

Testing attack function...
Original caption: A gold bus traveling on a single lane road
Original score: 0.7615, Original label: True
1
0.13542677462100983
0.13542677462100983
0.13542677462100983
0.13542677462100983
0.13542677462100983
0.13542677462100983
0.13542677462100983
0.13542677462100983
0.11250507086515427
0.11250507086515427
0.11250507086515427
0.11250507086515427
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.06935974210500717
0.069359742105007

In [29]:
# Evaluation Framework
def evaluate_attack(val_pairs: list, attack_function, alpha: float, beta: float, budgets: dict, max_samples: int = None):
    """
    Evaluate attack function on validation pairs.
    
    Args:
        val_pairs: List of validation pairs
        attack_function: Attack function to evaluate
        alpha, beta: Calibrated parameters
        budgets: Attack budgets dictionary
        max_samples: Limit number of samples (None = all)
        
    Returns:
        Dictionary with evaluation metrics
    """
    
    print(f"Starting evaluation...")
    
    # Limit samples if specified
    eval_pairs = val_pairs[:max_samples] if max_samples else val_pairs
    print(f"Evaluating on {len(eval_pairs)} samples")
    
    results = []
    total_success = 0
    total_token_cost = 0
    total_pixel_cost = 0
    total_query_cost = 0
    
    for i, pair in enumerate(tqdm(eval_pairs, desc="Attacking")):
        # Create fresh API instance for each sample
        api = BlackBoxAPI(alpha, beta, q_max=budgets['Q_MAX'])
        
        # Load image
        image = np.array(load_image_from_pair(pair))
        caption = pair['caption']
        
        try:
            # Run attack
            result = attack_function(image, caption, api, budgets)
            
            # Validate budget constraints
            budget_valid = (
                result['token_cost'] <= budgets['T_MAX'] and
                result['pixel_cost'] <= budgets['P_MAX'] and  
                result['query_cost'] <= budgets['Q_MAX']
            )
            
            if not budget_valid:
                print(f"Sample {i}: Budget violation!")
                print(f"   Tokens: {result['token_cost']}/{budgets['T_MAX']}")
                print(f"   Pixels: {result['pixel_cost']}/{budgets['P_MAX']}")  
                print(f"   Queries: {result['query_cost']}/{budgets['Q_MAX']}")
                result['success'] = False  # Invalid attacks count as failures
            
            results.append(result)
            
            if result['success']:
                total_success += 1
            total_token_cost += result['token_cost']
            total_pixel_cost += result['pixel_cost']
            total_query_cost += result['query_cost']
                
        except Exception as e:
            print(f"Sample {i}: Attack failed with error: {e}")
            # Add failed result
            results.append({
                'success': False,
                'token_cost': budgets['T_MAX'],  # Penalize failures
                'pixel_cost': budgets['P_MAX'], 
                'query_cost': budgets['Q_MAX'],
                'error': str(e)
            })
    
    # Calculate metrics
    n_samples = len(results)
    asr = total_success / n_samples  # Attack Success Rate
    anc = (10*total_token_cost + total_pixel_cost) / n_samples  # Average Number of Changes  
    aq = total_query_cost / n_samples  # Average Queries
    
    # Final score: ASR - 0.5*ANC - 0.1*(AQ/Q_MAX)
    score = asr - 0.5 * (anc / (10*budgets['T_MAX'] + budgets['P_MAX'])) - 0.1 * (aq / budgets['Q_MAX'])
    
    evaluation_result = {
        'ASR': asr,
        'ANC': anc, 
        'AQ': aq,
        'Score': score,
        'n_samples': n_samples,
        'total_success': total_success,
        'avg_token_cost': total_token_cost / n_samples,
        'avg_pixel_cost': total_pixel_cost / n_samples,
        'budgets': budgets,
        'results': results
    }
    
    return evaluation_result

# Run Evaluation
print("Running evaluation on validation set...")

# Define attack budgets
attack_budgets = {
    'T_MAX': 10,     # Maximum token edits per sample
    'P_MAX': 100,   # Maximum pixel edits per sample  
    'Q_MAX': 100    # Maximum queries per sample
}

# Evaluate on subset first (faster for testing)
print("Running on first 50 samples for quick testing...")
eval_result = evaluate_attack(
    val_pairs=val_pairs, 
    attack_function=attack,
    alpha=alpha,
    beta=beta, 
    budgets=attack_budgets,
    max_samples=50  # Quick test on 50 samples
)

# Print results
print(f"\nEVALUATION RESULTS (50 samples):")
print(f"{'='*50}")
print(f"Attack Success Rate (ASR): {eval_result['ASR']:.1%}")
print(f"Average Number of Changes (ANC): {eval_result['ANC']:.2f}")  
print(f"Average Queries (AQ): {eval_result['AQ']:.1f}")
print(f"Final Score: {eval_result['Score']:.4f}")
print(f"{'='*50}")
print(f"Budget Usage:")
print(f"  Avg Token Cost: {eval_result['avg_token_cost']:.2f}/{attack_budgets['T_MAX']}")
print(f"  Avg Pixel Cost: {eval_result['avg_pixel_cost']:.2f}/{attack_budgets['P_MAX']}")  
print(f"  Avg Query Cost: {eval_result['AQ']:.1f}/{attack_budgets['Q_MAX']}")


Running evaluation on validation set...
Running on first 50 samples for quick testing...
Starting evaluation...
Evaluating on 50 samples


Attacking:   0%|          | 0/50 [00:00<?, ?it/s]

Original caption: A gold bus traveling on a single lane road
Original score: 0.7744, Original label: True
1
0.13234369456768036
0.13234369456768036
0.13234369456768036
0.13234369456768036
0.13234369456768036
0.13234369456768036
0.13234369456768036
0.13234369456768036
0.11493301391601562
0.11493301391601562
0.11493301391601562
0.11493301391601562
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.06923467665910721
0.0692346766

Attacking:   2%|▏         | 1/50 [00:01<00:53,  1.09s/it]

0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.002429043175652623
0.00242904317

...

Attacking:  38%|███▊      | 19/50 [00:20<00:33,  1.09s/it]

0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114
0.03252388909459114


Attacking:  38%|███▊      | 19/50 [00:20<00:34,  1.10s/it]

0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373
0.23134812712669373


KeyboardInterrupt: 

In [ ]:
# Full Evaluation (Uncomment when ready to test your attack)

def run_full_evaluation():
    """Run evaluation on all 1000 validation samples."""
    print("Running FULL evaluation on all 1000 validation samples...")
    print("This may take several minutes depending on your attack implementation.")
    
    full_result = evaluate_attack(
        val_pairs=val_pairs,
        attack_function=attack, 
        alpha=alpha,
        beta=beta,
        budgets=attack_budgets,
        max_samples=None  # All samples
    )
    
    print(f"\nFINAL EVALUATION RESULTS:")
    print(f"{'='*60}")
    print(f"Attack Success Rate (ASR): {full_result['ASR']:.1%}")
    print(f"Average Number of Changes (ANC): {full_result['ANC']:.2f}")
    print(f"Average Queries (AQ): {full_result['AQ']:.1f}")
    print(f"Final Score: {full_result['Score']:.4f}")
    print(f"{'='*60}")
    
    return full_result

# Uncomment the line below when ready to run full evaluation:
full_results = run_full_evaluation()


Running FULL evaluation on all 1000 validation samples...
This may take several minutes depending on your attack implementation.
Starting evaluation...
Evaluating on 1000 samples


Attacking:   0%|          | 3/1000 [00:00<00:50, 19.92it/s]

Original score: 0.7744, Original label: True
Final score: 0.5207
Original score: 0.2920, Original label: False
Final score: 0.3240
Original score: 0.3550, Original label: False
Final score: 0.3636
Original score: 0.5362, Original label: True
Final score: 0.3820
Original score: 0.7966, Original label: True
Final score: 0.6406


Attacking:   1%|          | 9/1000 [00:00<00:42, 23.33it/s]

Original score: 0.7098, Original label: True
Final score: 0.3760
Original score: 0.7137, Original label: True
Final score: 0.5042
Original score: 0.4313, Original label: False
Final score: 0.3687
Original score: 0.3835, Original label: False
Final score: 0.4848
Original score: 0.2675, Original label: False
Final score: 0.3527


...

Original score: 0.5777, Original label: True
Final score: 0.4568
Original score: 0.6586, Original label: True
Final score: 0.3702
Original score: 0.4192, Original label: False
Final score: 0.3230
Original score: 0.6870, Original label: True
Final score: 0.3437
Original score: 0.2763, Original label: False
Final score: 0.4081


Attacking:  99%|█████████▉| 993/1000 [00:41<00:00, 24.00it/s]

Original score: 0.1959, Original label: False
Final score: 0.2983
Original score: 0.4744, Original label: False
Final score: 0.2768
Original score: 0.6841, Original label: True
Final score: 0.3827
Original score: 0.3111, Original label: False
Final score: 0.2730
Original score: 0.2622, Original label: False
Final score: 0.3659


Attacking: 100%|██████████| 1000/1000 [00:41<00:00, 24.17it/s]

Original score: 0.2080, Original label: False
Final score: 0.3496
Original score: 0.2476, Original label: False
Final score: 0.3877
Original score: 0.4869, Original label: False
Final score: 0.3172
Original score: 0.5719, Original label: True
Final score: 0.4861
Original score: 0.3726, Original label: False
Final score: 0.4146

FINAL EVALUATION RESULTS:
Attack Success Rate (ASR): 43.3%
Average Number of Changes (ANC): 37.78
Average Queries (AQ): 2.0
Final Score: 0.3366


## Baseline scoring

In [ ]:
def baseline_attack(image_np_uint8: np.ndarray, caption_str: str, api: BlackBoxAPI, budgets: dict) -> dict:

    # TRIVIAL BASELINE - Students should replace this!
    # This baseline just returns the original inputs without any attack
    
    original_image = image_np_uint8.copy()
    original_caption = caption_str
    
    # Get original score to determine target (flip the decision)
    original_score = api.score(original_image, original_caption)

    final_image = original_image        # Comment out this line when implementing image attacks
    final_caption = original_caption    # Comment out this line when implementing text attacks
    
    # Get final score  
    final_score = api.score(final_image, final_caption)
    
    # Check if attack succeeded (decision flipped)
    original_decision = original_score > 0.5
    final_decision = final_score > 0.5
    success = (original_decision != final_decision)
    
    # Calculate costs
    token_cost = token_edit_cost(original_caption, final_caption)
    pixel_cost = pixel_edit_cost(original_image, final_image)
    query_cost = api.query_count
    
    return {
        'success': success,
        'image': final_image,
        'caption': final_caption,
        'token_cost': token_cost,
        'pixel_cost': pixel_cost,  
        'query_cost': query_cost,
        'original_score': original_score,
        'final_score': final_score
    }

In [ ]:


# Run Evaluation
print("Running evaluation on validation set...")

# Define attack budgets
attack_budgets = {
    'T_MAX': 10,     # Maximum token edits per sample
    'P_MAX': 100,   # Maximum pixel edits per sample  
    'Q_MAX': 100    # Maximum queries per sample
}

# Evaluate on subset first (faster for testing)
print("Running on first 50 samples for quick testing...")
eval_result = evaluate_attack(
    val_pairs=val_pairs, 
    attack_function=baseline_attack,
    alpha=alpha,
    beta=beta, 
    budgets=attack_budgets,
    max_samples=50  # Quick test on 50 samples
)

# Print results
print(f"\nEVALUATION RESULTS (50 samples):")
print(f"{'='*50}")
print(f"Attack Success Rate (ASR): {eval_result['ASR']:.1%}")
print(f"Average Number of Changes (ANC): {eval_result['ANC']:.2f}")  
print(f"Average Queries (AQ): {eval_result['AQ']:.1f}")
print(f"Final Score: {eval_result['Score']:.4f}")
print(f"{'='*50}")
print(f"Budget Usage:")
print(f"  Avg Token Cost: {eval_result['avg_token_cost']:.2f}/{attack_budgets['T_MAX']}")
print(f"  Avg Pixel Cost: {eval_result['avg_pixel_cost']:.2f}/{attack_budgets['P_MAX']}")  
print(f"  Avg Query Cost: {eval_result['AQ']:.1f}/{attack_budgets['Q_MAX']}")
print(f"\nNOTE: This is a trivial baseline (0% ASR expected)")
print(f"Students should implement sophisticated attacks to improve ASR!")

Running evaluation on validation set...
Running on first 50 samples for quick testing...
Starting evaluation...
Evaluating on 50 samples


Attacking: 100%|██████████| 50/50 [00:01<00:00, 28.00it/s]


EVALUATION RESULTS (50 samples):
Attack Success Rate (ASR): 0.0%
Average Number of Changes (ANC): 0.00
Average Queries (AQ): 2.0
Final Score: -0.0020
Budget Usage:
  Avg Token Cost: 0.00/10
  Avg Pixel Cost: 0.00/100
  Avg Query Cost: 2.0/100

NOTE: This is a trivial baseline (0% ASR expected)
Students should implement sophisticated attacks to improve ASR!


In [ ]:
# Full Evaluation (Uncomment when ready to test your attack)

def run_full_evaluation():
    """Run evaluation on all 1000 validation samples."""
    print("Running FULL evaluation on all 1000 validation samples...")
    print("This may take several minutes depending on your attack implementation.")
    
    full_result = evaluate_attack(
        val_pairs=val_pairs,
        attack_function=baseline_attack, 
        alpha=alpha,
        beta=beta,
        budgets=attack_budgets,
        max_samples=None  # All samples
    )
    
    print(f"\nFINAL EVALUATION RESULTS:")
    print(f"{'='*60}")
    print(f"Attack Success Rate (ASR): {full_result['ASR']:.1%}")
    print(f"Average Number of Changes (ANC): {full_result['ANC']:.2f}")
    print(f"Average Queries (AQ): {full_result['AQ']:.1f}")
    print(f"Final Score: {full_result['Score']:.4f}")
    print(f"{'='*60}")
    
    return full_result

# Uncomment the line below when ready to run full evaluation:
full_results = run_full_evaluation()

print("To run full evaluation on all 1000 samples:")
print("Uncomment: full_results = run_full_evaluation()")
print("\nCurrent status: Framework ready for student implementations!")

Running FULL evaluation on all 1000 validation samples...
This may take several minutes depending on your attack implementation.
Starting evaluation...
Evaluating on 1000 samples


Attacking: 100%|██████████| 1000/1000 [00:36<00:00, 27.70it/s]


FINAL EVALUATION RESULTS:
Attack Success Rate (ASR): 0.3%
Average Number of Changes (ANC): 0.00
Average Queries (AQ): 2.0
Final Score: 0.0010
To run full evaluation on all 1000 samples:
Uncomment: full_results = run_full_evaluation()

Current status: Framework ready for student implementations!
